<a href="https://colab.research.google.com/github/saheedniyi02/100-days-of-machine-learning-code/blob/master/Untitled4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import pandas as pd

In [ ]:
pip install catboost

In [ ]:
train=pd.read_csv("Train_maskedv2.csv",index_col=0)
test=pd.read_csv("Test_maskedv2.csv",index_col=0)






In [ ]:
def num_to_cat(a):
    if a<0.2:
        return "Very Low"
    elif a<0.4:
        return "Low"
    elif a<0.6:
        return "Good"
    elif a<0.8:
        return "Very Good"
    else:
        return "Great"

In [ ]:
def cat_num(i):
	if i <0.1:
		return "1st"
	elif i <0.2:
		return "2nd"
	elif i <0.3:
		return "3rd"
	elif i <0.4:
		return "4th"
	elif i <0.5:
		return "5th"
	elif i <0.6:
		return "6th"
	elif i <0.7:
		return "'7th"
	elif i <0.8:
		return "8th"
	elif i <0.9:
		return "9th"
	else:
		return "10th"

In [ ]:
target=train['target_pct_vunerable']
train.drop('target_pct_vunerable',axis=1,inplace=True)

In [ ]:
from sklearn.model_selection import cross_val_score,ShuffleSplit,train_test_split,KFold
from lightgbm import LGBMRegressor
from sklearn.metrics import mean_squared_error
from sklearn.neural_network import MLPRegressor
from sklearn.linear_model import LinearRegression,Lasso,Ridge
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler,PolynomialFeatures,MinMaxScaler,RobustScaler
from sklearn.decomposition import PCA
from sklearn.experimental import enable_hist_gradient_boosting
from catboost import CatBoostRegressor
from sklearn.ensemble import GradientBoostingRegressor,RandomForestRegressor,ExtraTreesRegressor,StackingRegressor,HistGradientBoostingRegressor
from sklearn.svm import SVR
from lightgbm import LGBMRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.cluster import KMeans
from xgboost import XGBRegressor

In [ ]:
pipe_kmeans=Pipeline([("s",MinMaxScaler()),("km",KMeans(n_clusters=7,random_state=0))])
pipe_pca=Pipeline([("sc",StandardScaler()),("p",PCA(n_components=1,random_state=0))])

In [ ]:
for data in [train,test]:
    data["total_households"]=data["total_households"].astype("i")
    data["total_individuals"]=data["total_individuals"].astype("i")
    data['average individual per household for world']=data['total_individuals']/data['total_households']
    data["psa_06"]=data["psa_02"]+data["psa_03"]
    data["rare_languages"]=data["lan_02"]+data["lan_03"]+data["lan_04"]+data["lan_05"]+data["lan_06"]+data["lan_07"]
    +data["lan_09"]+data["lan_10"]+data["lan_11"]   
    data["new1"]=data["psa_00"]/data["psa_01"]
    data["new2"]=data["psa_02"]+data["psa_03"]
    luxury=["stv_00","car_00","lln_00"]
    
    

In [ ]:
for data in [train,test]:
    data["min_lux"]=np.min(data[luxury],axis=1)

In [ ]:
data=pd.concat([train,test])

data["kmeans"]=pipe_kmeans.fit_predict(data)
data["pca"]=pipe_pca.fit_transform(data.drop("kmeans",axis=1))[:,0]

In [ ]:
train=data.iloc[:train.shape[0]]
test=data.iloc[train.shape[0]:]

In [ ]:
train.drop("W0TZK41",inplace=True)
target.drop("W0TZK41",inplace=True)

/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:4174: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [ ]:
target

ward
9D9BEUB    1.739801
RERH3XM    1.993381
GJWA3BO    0.038340
GW6VRB7    7.411006
CN9JZJC    8.223907
             ...   
HFWMU2J    3.500868
8LVBHRG    0.116460
5WDYHUG    0.958828
7ODH7UJ    1.024934
UDW539J    5.283125
Name: target_pct_vunerable, Length: 3173, dtype: float64

In [ ]:
train=pd.get_dummies(train)
test=pd.get_dummies(test)

In [ ]:
pipe_grb=Pipeline([("scal",StandardScaler()),("model",GradientBoostingRegressor(criterion="mse",random_state=0,verbose=2,max_depth=6,n_estimators=260,learning_rate=0.05))])
pipe_svm=Pipeline([("scal",StandardScaler()),("svr",SVR())])
pipe_kn=Pipeline([("scal",StandardScaler()),("svr",KNeighborsRegressor(n_neighbors=11))])
pipe_lasso=Pipeline([("poly",PolynomialFeatures()),("scal",StandardScaler()),("lasso",Lasso())])
pipe_ridge=Pipeline([("scal",MinMaxScaler()),("rid",Ridge())])
pipe_mlp=Pipeline([("scal",StandardScaler()),("mlp",MLPRegressor(random_state=0,max_iter=150,verbose=2))])
pipe_hgrb=Pipeline([("scal",StandardScaler()),("hist",HistGradientBoostingRegressor(random_state=0,verbose=2))])
pipe_rfg=RandomForestRegressor(criterion="mse",n_estimators=210,random_state=0)
pipe_xrfg=ExtraTreesRegressor(n_estimators=150,random_state=0)
pipe_cat=CatBoostRegressor(random_state=0,iterations=2000)
pipe_lgb=Pipeline([("scal",StandardScaler()),("lgb",LGBMRegressor(random_state=0,verbose=2))])
pipe_xgb=Pipeline([("scal",StandardScaler()),("lgb",XGBRegressor(random_state=0,verbose=2))])

In [ ]:
estimators=[("grb",pipe_grb),
           ("kn",pipe_kn),
           ("sv",pipe_svm),
           ("ls",pipe_lasso),
           ("ml",pipe_mlp),
           ("rg",pipe_ridge),
           ("hist",pipe_hgrb),
           ("for",pipe_rfg),
           ("xtr",pipe_xrfg),
           ("cat",pipe_cat),
           ("lgb",pipe_lgb),
           ("xg",pipe_xgb)]

In [ ]:
pipe=StackingRegressor(estimators=estimators,final_estimator=pipe_ridge,verbose=3)

In [ ]:
sss=KFold(n_splits=5)
predictions_frame=pd.DataFrame(columns=[1,2,3,4,5])
train_score=[]
test_score=[]
rmse=[]
preds=pd.DataFrame(columns=[1,2,3,4,5,6,7])
for i,(train_index,test_index) in enumerate(sss.split(train,target)):
    train_ss=train.iloc[train_index]
    val_ss=train.iloc[test_index]
    y_ss=target.iloc[train_index]
    y_val_ss=target.iloc[test_index]
    pipe.fit(train_ss,y_ss)
    pred=pipe.predict(val_ss)
    prediction=pipe.predict(test)
    predictions_frame[i+1]=prediction
    test_score.append(pipe.score(val_ss,y_val_ss))
    train_score.append(pipe.score(train_ss,y_ss))
    rmse.append(mean_squared_error(y_val_ss,pred))
print(f"train_score{train_score}")
print(f"test_score{test_score}")
print(f"rmse{rmse}")

      Iter       Train Loss   Remaining Time 
         1         149.3773           19.08s
         2         137.7285           18.89s
         3         127.2038           18.93s
         4         117.7267           18.91s
         5         109.0403           18.79s
         6         101.0702           18.75s
         7          93.8982           18.77s
         8          87.3048           18.68s
         9          81.1744           18.70s
        10          75.5990           18.56s
        11          70.4740           18.44s
        12          65.9227           18.41s
        13          61.6825           18.32s
        14          57.7987           18.26s
        15          54.1561           18.21s
        16          50.9419           18.14s
        17          48.0106           18.07s
        18          45.2376           18.10s
        19          42.7314           18.02s
        20          40.3524           17.98s
        21          38.2476           17.91s
        2

/usr/local/lib/python3.6/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:571: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (150) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


1 tree, 31 leaves, max depth = 9, in 0.023s
[7/100] 1 tree, 31 leaves, max depth = 9, in 0.018s
[8/100] 1 tree, 31 leaves, max depth = 8, in 0.019s
[9/100] 1 tree, 31 leaves, max depth = 9, in 0.029s
[10/100] 1 tree, 31 leaves, max depth = 9, in 0.020s
[11/100] 1 tree, 31 leaves, max depth = 9, in 0.024s
[12/100] 1 tree, 31 leaves, max depth = 12, in 0.017s
[13/100] 1 tree, 31 leaves, max depth = 10, in 0.022s
[14/100] 1 tree, 31 leaves, max depth = 11, in 0.018s
[15/100] 1 tree, 31 leaves, max depth = 8, in 0.029s
[16/100] 1 tree, 31 leaves, max depth = 8, in 0.015s
[17/100] 1 tree, 31 leaves, max depth = 8, in 0.021s
[18/100] 1 tree, 31 leaves, max depth = 8, in 0.014s
[19/100] 1 tree, 31 leaves, max depth = 7, in 0.017s
[20/100] 1 tree, 31 leaves, max depth = 12, in 0.016s
[21/100] 1 tree, 31 leaves, max depth = 11, in 0.018s
[22/100] 1 tree, 31 leaves, max depth = 10, in 0.016s
[23/100] 1 tree, 31 leaves, max depth = 11, in 0.016s
[24/100] 1 tree, 31 leaves, max depth = 9, in 0.017

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


      Iter       Train Loss   Remaining Time 
         1         149.1277           14.93s
         2         137.5673           14.96s
         3         126.9988           14.97s
         4         117.4615           15.21s
         5         108.7384           15.11s
         6         100.8220           15.01s
         7          93.5077           15.04s
         8          86.9690           15.12s
         9          80.9913           15.15s
        10          75.3925           15.07s
        11          70.1197           14.98s
        12          65.3719           15.02s
        13          61.0611           14.92s
        14          57.0834           14.82s
        15          53.4350           14.75s
        16          50.0404           14.71s
        17          47.1166           14.63s
        18          44.2171           14.54s
        19          41.7200           14.46s
        20          39.2625           14.41s
        21          37.0391           14.38s
        2

...

[03:45:42] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    1.4s remaining:    0.0s


[03:45:42] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[03:45:43] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[03:45:44] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


[Parallel(n_jobs=1)]: Done   5 out of   5 | elapsed:    3.6s finished


train_score[0.9938036867918827, 0.9936833119751753, 0.9951796779378438, 0.9953061840116649, 0.9948182103660225]
test_score[0.8043229945760837, 0.8231317537105476, 0.8111741107214329, 0.8174199193160755, 0.851409246747113]
rmse[32.04547730625214, 27.861601671040564, 30.532418706566546, 30.432824342910557, 24.16925345034509]


In [ ]:
prediction=np.mean(np.abs(predictions_frame[[2,3,4,5]]),axis=1)

In [ ]:
prediction

0       13.306140
1       31.266766
2        6.185330
3        2.376259
4        0.506310
          ...    
1097    15.621814
1098     0.727690
1099     4.873700
1100     0.301741
1101     0.769117
Length: 1102, dtype: float64

In [ ]:
sub=pd.DataFrame({"ward":test.index,"target_pct_vunerable":prediction}).set_index("ward")

In [ ]:
sub["target_pct_vunerable"]=np.abs(sub["target_pct_vunerable"])

In [ ]:
sub.to_csv("sub.csv")